#  Madagascar Vulnerability Index - Indicator Explorer Notebook

*author@SingerG, Abt Associates, November 2023*

### Introduction
From the top menu, open the 'Kernel" dropdown and select 'Restart and Run All' in order to start the tool.

The purpose of this tool is enable the user to adjust the weighted domains in the Vulnerability Index.

*If you would like to view each of the indicators and domains in a WebMap, please open the following link in a new window: (LINK TO WEBMAP).*

In [5]:
# !pip install geopandas folium
# !pip install ipywidgets

In [9]:
%%time

def Run_Vulnerability_Index_Explorer(geojson_path):
    '''
    This is the main function that loads the spatial dataframe from a given item ID.
    '''
    # Import Modules
    import pandas as pd
    import ipywidgets as widgets
    from IPython.display import display, HTML
    import io
    import base64
    import geopandas as gpd
    from shapely.geometry import Point
    import folium
    from folium.plugins import MarkerCluster
    import json

    # Define function to calculate Vulnerability Index (Average of each (Percentile * Weight) per Indicator)
    def calculate_products_and_average(percentile_rank_df):
        # Create a new DataFrame for the result
        result_df = pd.DataFrame()

        # Iterate through the column sets and calculate the product
        percentile_rank_columns = [col for col in percentile_rank_df.columns if col.endswith('_Percentile_Rank')]
        for col in percentile_rank_columns:
            stem = col.rsplit('_Percentile_Rank', 1)[0]
            weight_col = stem + '_weight'
            result_df[stem] = percentile_rank_df[col] * percentile_rank_df[weight_col]

        # Calculate the row-wise sum
        result_df['Vulnerability_Index'] = round(result_df.sum(axis=1),3)

        # Concatenate the result_df with the original df
        combined_df = pd.concat([percentile_rank_df, result_df], axis=1)
        combined_df['Vulnerability_Index_Percentile'] = round(combined_df['Vulnerability_Index'].rank(pct=True)*100)
        return combined_df

    # Define a function to calculate Percentile_Rank
    def create_percentile_rank_index(sdf, columns_to_rank):
        # Initialize a new DataFrame to store percentile rank values
        percentile_rank_df = pd.DataFrame()
        # Create an empty list to store the new percentile_rank cols
        percentile_rank_cols = []
        weight_cols = []
        # Calculate percentile ranks for the specified columns and store them in the new DataFrame
        for column in columns_to_rank:
            percentile_rank_df[column + '_Percentile_Rank'] = sdf[column].rank(pct=True)*100
    #         percentile_rank_df[column + '_Percentile_Rank'] = dataframe[column]
            percentile_rank_cols.append(column + '_Percentile_Rank')
            # Add Weight Col
            percentile_rank_df[column + '_weight'] = .1
            weight_cols.append(column + '_weight')

    #     Add the final index to the new DataFrame
        percentile_rank_df = calculate_products_and_average(percentile_rank_df)
    #     percentile_rank_df['Index'] = (percentile_rank_df[percentile_rank_cols].prod(axis=1)) * (percentile_rank_df[weight_cols].prod(axis=1))
        percentile_rank_df= pd.concat([sdf, percentile_rank_df], axis = 1)
        return percentile_rank_df, percentile_rank_cols, weight_cols

    # Define a function to update the DataFrame with the values from the widgets
    # def update_dataframe(change, output_widget, adj_weight_cols, input_widgets):
    def update_dataframe(change):
        output_widget.clear_output()
        for column in adj_weight_cols:
            df[column] = [input_widgets[column].value] * len(df)

        # Create a new DataFrame for the result
        result_df = pd.DataFrame()

        # Iterate through the column sets and calculate the product
        percentile_rank_columns = [col for col in df.columns if col.endswith('_Percentile_Rank')]
        for col in percentile_rank_columns:
            stem = col.rsplit('_Percentile_Rank', 1)[0]
            weight_col = stem + '_weight'
            result_df[stem] = df[col] * df[weight_col]

        # Calculate the row-wise sum
        df['Vulnerability_Index'] = round(result_df.sum(axis=1),3)
        df['Vulnerability_Index_Percentile'] = round(df['Vulnerability_Index'].rank(pct=True)*100)
    #     calculate_products_and_average(df)
        with output_widget:
            display(df[['OBJECTID', 'SOURCE_ID', 'Vulnerability_Index','Vulnerability_Index_Percentile']])

    # Define a function to update the map
    def update_map(m1):
        # Create a choropleth map based on the specified column
        updated_layer = folium.Choropleth(
            geo_data= df,
            name = 'Weighted Vulnerability Index',
            data = df,
            columns=['OBJECTID','Vulnerability_Index_Percentile'],
            key_on='feature.id',
            fill_color='RdYlBu_r',
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='Weighted_Vulnerability_Index_Percentile'
        )

        updated_layer.add_to(m1)

        # Remove existing LayerControl if it exists
        for element in m1._children:
            if isinstance(element, folium.map.LayerControl):
                m1._children.pop(m1._children.index(element))

        # Add LayerControl to the map
        folium.LayerControl().add_to(m1)

        # Apply custom CSS style to the legend background
        legend_style = """
            <style>
                .leaflet-control .leaflet-control-layers, .leaflet-control .leaflet-control-layers-expanded {
                    background-color: #ffffff;  /* Change this to your desired background color */
                }
            </style>
        """
        m1.get_root().html.add_child(folium.Element(legend_style))


    # Define a function to be called when the "Update" button is clicked
    def on_update_button_click(click):
        print("Please wait for map to update")
        update_dataframe(None)

        # Clear Existing layers on the map
        m1 = display_map(df)
        update_map(m1)
        print("Map update complete.")
        # Create a download link widget
        download_link = create_download_link(df)
        # Display the download link
        display(download_link)

    # Define Indicator Columns
    def define_columns_to_rank():
        # columns_to_rank = [col for col in sdf.columns if '_PREPROCESSED' in col]
        columns_to_rank = ['STUNTING_SUM_PREPROCESSED',
                           'sum_Length_METERS_PREPROCESSED',
                           'anomaly_rate_PREPROCESSED',
                           'IPC_Average_PREPROCESSED',
                           'Affected_ADJ_PREPROCESSED',
                           'CropDMGHA_ADJ_PREPROCESSED',
                           'DahaloFlagActor1Cnt_PREPROCESSE',
                          'DahaloFlagActor2Cnt_PREPROCESSE',
                           'market_price_volatility_PREPROC',
                          ]
        return(columns_to_rank)

    def display_map(df):
        # Create a Folium map centered around the GeoDataFrame
        map_center = [df['geometry'].centroid.y.mean(), df['geometry'].centroid.x.mean()]
        m1= folium.Map(location=map_center, zoom_start=7,
                      # width = '50%',
                      # height = '50%',
                      tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
                      attr = 'Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community')

        # Create a choropleth map based on the specified column
        folium.Choropleth(
            geo_data= df,
            name = 'Unweighted Vulnerability Index',
            data = df,
            columns=['OBJECTID','Vulnerability_Index_Percentile'],
            key_on='feature.id',
            fill_color='RdYlBu_r',
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='Vulnerability_Index_Percentile'
        ).add_to(m1)

        folium.LayerControl().add_to(m1)

        # Display the map
        return m1

    # Function to create a download link for DataFrame as CSV
    def create_download_link(df, filename='Updated_Indicator_Weights.csv'):
        cols_to_download = ['OBJECTID', 'SOURCE_ID', 'Vulnerability_Index','Vulnerability_Index_Percentile'] + rank_cols + adj_weight_cols
        csv_str = df[cols_to_download].to_csv(index=False)
        csv_bytes = csv_str.encode('utf-8')
        b64 = base64.b64encode(csv_bytes)
        payload = b64.decode()
        download_link = f'<a download="{filename}" href="data:text/csv;base64,{payload}" target="_blank">Download CSV with updated indicator weights and weighted vulnerability index </a>'
        return widgets.HTML(download_link)

    # Load Dataframe with Initial Vulnerability Index (Default Weights = 0.1)
    df = gpd.read_file(geojson_path)
    df, rank_cols, adj_weight_cols = create_percentile_rank_index(df, define_columns_to_rank())
    df = df.loc[:,~df.columns.duplicated()]
    m1 = display_map(df)
    display(m1)

    # Create a widget title
    VBox_Title = widgets.HTML(value = "<h2 style='font-weight: bold; text-decoration: underline; '>Vulnerability Index Percentile Map</h2>")

    # Create an "Update" button
    update_button = widgets.Button(description="Click to update")

    # Create an output widget to display the updated DataFrame
    output_widget = widgets.Output()

    # Create a dictionary to store the input widgets
    input_widgets = {}

    # Create input widgets for each column with the column name as the description
    for column in adj_weight_cols:
    #     input_widgets[column] = widgets.IntText(value=df[column][0], description=column)
        input_widgets[column] = widgets.FloatSlider(
            value=df[column][0],
            min=0,
            max=1,
            step=0.1,
            description=column.rsplit('_', 2)[0],
            orientation='horizontal',
            layout=widgets.Layout(width='50%'),  # Allows the label to expand as needed
            style={'description_width': '10%'},  # Prevents line breaks in the label text
            continuous_update=False,  # Prevents real-time updates
        )
        input_widgets[column].title = column  # Set the tooltip as the column name

    # Attach the update_dataframe function to the change events of the input widgets
    for column in adj_weight_cols:
        input_widgets[column].observe(update_dataframe, 'value')


    # Attach the on_update_button_click function to the button's click event
    update_button.on_click(on_update_button_click)

    # Display the input widgets, the "Update" button, and the updated DataFrame
    input_widgets_list = [input_widgets[column] for column in adj_weight_cols]

    # Create a widget title
    weight_slider_title = widgets.HTML(value = "<h3 style='font-weight: bold;'>Interactive Weight Slider</h3>")

    # Group widgets in VBox
    VBox = widgets.VBox([update_button, weight_slider_title, *input_widgets_list, output_widget])

    VBox.layout.width = '100%'
    VBox.layout.heigth = '300%'
    display(VBox)

    return(df)

CPU times: user 9 µs, sys: 0 ns, total: 9 µs
Wall time: 12.6 µs


### Run Vulnerability Index Explorer: Instructions
    1) Use the slider to adjust the indicator weights.
    2) Click the button underneathe the map to update the map.
    3) Once the map updates, you will have the option to download an excel file with your updated weighted indicators and vulnerability index.

In [10]:
%%time
df = Run_Vulnerability_Index_Explorer(geojson_path = r'https://raw.githubusercontent.com/TheDigitalGarbologist/Madagascar_VulnerabilityIndex/main/MadagascarCommunes_VI.geojson')



<timed exec>:155: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



CPU times: user 3.48 s, sys: 139 ms, total: 3.62 s
Wall time: 3.66 s


Support for third party widgets will remain active for the duration of the session. To disable support:

In [ ]:
import sys

# Get a list of active module names
active_modules = list(sys.modules.keys())
print(active_modules)

['sys', 'builtins', '_frozen_importlib', '_imp', '_thread', '_warnings', '_weakref', '_io', 'marshal', 'posix', '_frozen_importlib_external', 'time', 'zipimport', '_codecs', 'codecs', 'encodings.aliases', 'encodings', 'encodings.utf_8', '_signal', '_abc', 'abc', 'io', '__main__', 'types', 'enum', '_sre', 'sre_constants', 'sre_parse', 'sre_compile', '_collections_abc', 'itertools', 'keyword', '_operator', 'operator', 'reprlib', '_collections', 'collections', '_functools', 'functools', '_locale', 'copyreg', 're', 'warnings', '_stat', 'stat', 'genericpath', 'posixpath', 'os.path', 'os', '_sitebuiltins', '_distutils_hack', 'importlib._bootstrap', 'importlib._bootstrap_external', 'importlib', 'importlib._abc', 'contextlib', 'importlib.util', 'importlib.machinery', 'google', 'google.cloud', 'google.logging', 'google.iam', 'mpl_toolkits', 'sphinxcontrib', 'sitecustomize', 'site', 'runpy', 'ipykernel._version', '_json', 'json.scanner', 'json.decoder', 'json.encoder', 'json', 'errno', 'signal',